In [1]:
import tensorflow as tf
import numpy as np

In [2]:
def fc(inputs, num_out, name, activation_fn=None, biased=True):
    w_init = tf.random_normal_initializer(stddev=0.02)
    return tf.layers.dense(inputs=inputs, units=num_out, activation=activation_fn, kernel_initializer=w_init, use_bias=biased, name=name)


def concat(inputs, axis, name):
    return tf.concat(values=inputs, axis=axis, name=name)

def batch_normalization(inputs, is_training, name, activation_fn=None):
    output = tf.layers.batch_normalization(
                    inputs,
                    momentum=0.95,
                    epsilon=1e-5,
                    training=is_training,
                    name=name
                )

    if activation_fn is not None:
        output = activation_fn(output)

    return output

def reshape(inputs, shape, name):
    return tf.reshape(inputs, shape, name)

def Conv2d(input, k_h, k_w, c_o, s_h, s_w, name, activation_fn=None, padding='VALID', biased=False):
    c_i = input.get_shape()[-1]
    w_init = tf.random_normal_initializer(stddev=0.02)

    convolve = lambda i, k: tf.nn.conv2d(i, k, [1, s_h, s_w, 1], padding=padding)
    with tf.variable_scope(name) as scope:
        kernel = tf.get_variable(name='weights', shape=[k_h, k_w, c_i, c_o], initializer=w_init)
        output = convolve(input, kernel)

        if biased:
            biases = tf.get_variable(name='biases', shape=[c_o])
            output = tf.nn.bias_add(output, biases)
        if activation_fn is not None:
            output = activation_fn(output, name=scope.name)

        return output

def add(inputs, name):
    return tf.add_n(inputs, name=name)

def UpSample(inputs, size, method, align_corners, name):
    return tf.image.resize_images(inputs, size, method, align_corners)

def flatten(input, name):
    input_shape = input.get_shape()
    dim = 1
    for d in input_shape[1:].as_list():
        dim *= d
        input = tf.reshape(input, [-1, dim])
    
    return input

class Generator:
    def __init__(self, input_z, input_rnn, is_training, reuse):
        self.input_z = input_z
        self.input_rnn = input_rnn
        self.is_training = is_training
        self.reuse = reuse
        self.t_dim = 128
        self.gf_dim = 128
        self.image_size = 64
        self.c_dim = 3
        self._build_model()

    def _build_model(self):
        s = self.image_size
        s2, s4, s8, s16 = int(s/2), int(s/4), int(s/8), int(s/16)

        gf_dim = self.gf_dim
        t_dim = self.t_dim
        c_dim = self.c_dim

        with tf.variable_scope("generator", reuse=self.reuse):
            net_txt = fc(inputs=self.input_rnn, num_out=t_dim, activation_fn=tf.nn.leaky_relu, name='rnn_fc')
            net_in = concat([self.input_z, net_txt], axis=1, name='concat_z_txt')

            net_h0 = fc(inputs=net_in, num_out=gf_dim*8*s16*s16, name='g_h0/fc', biased=False)
            net_h0 = batch_normalization(net_h0, activation_fn=None, is_training=self.is_training, name='g_h0/batch_norm')
            net_h0 = reshape(net_h0, [-1, s16, s16, gf_dim*8], name='g_h0/reshape')
            
            net = Conv2d(net_h0, 1, 1, gf_dim*2, 1, 1, name='g_h1_res/conv2d')
            net = batch_normalization(net, activation_fn=tf.nn.relu, is_training=self.is_training, name='g_h1_res/batch_norm')
            net = Conv2d(net, 3, 3, gf_dim*2, 1, 1, name='g_h1_res/conv2d2', padding='SAME')
            net = batch_normalization(net, activation_fn=tf.nn.relu, is_training=self.is_training, name='g_h1_res/batch_norm2')
            net = Conv2d(net, 3, 3, gf_dim*8, 1, 1, name='g_h1_res/conv2d3', padding='SAME')
            net = batch_normalization(net, activation_fn=None, is_training=self.is_training, name='g_h1_res/batch_norm3')

            net_h1 = add([net_h0, net], name='g_h1_res/add')
            net_h1_output = tf.nn.relu(net_h1)
            
            net_h2 = UpSample(net_h1_output, size=[s8, s8], method=1, align_corners=False, name='g_h2/upsample2d')
            net_h2 = Conv2d(net_h2, 3, 3, gf_dim*4, 1, 1, name='g_h2/conv2d', padding='SAME')
            net_h2 = batch_normalization(net_h2, activation_fn=None, is_training=self.is_training, name='g_h2/batch_norm')

            net = Conv2d(net_h2, 1, 1, gf_dim, 1, 1, name='g_h3_res/conv2d')
            net = batch_normalization(net, activation_fn=tf.nn.relu, is_training=self.is_training, name='g_h3_res/batch_norm')
            net = Conv2d(net, 3, 3, gf_dim, 1, 1, name='g_h3_res/conv2d2', padding='SAME')
            net = batch_normalization(net, activation_fn=tf.nn.relu, is_training=self.is_training, name='g_h3_res/batch_norm2')
            net = Conv2d(net, 3, 3, gf_dim*4, 1, 1, name='g_h3_res/conv2d3', padding='SAME')
            net = batch_normalization(net, activation_fn=None, is_training=self.is_training, name='g_h3_res/batch_norm3')
            
            net_h3 = add([net_h2, net], name='g_h3/add')
            net_h3_outputs = tf.nn.relu(net_h3)

            net_h4 = UpSample(net_h3_outputs, size=[s4, s4], method=1, align_corners=False, name='g_h4/upsample2d')
            net_h4 = Conv2d(net_h4, 3, 3, gf_dim*2, 1, 1, name='g_h4/conv2d', padding='SAME')
            net_h4 = batch_normalization(net_h4, activation_fn=tf.nn.relu, is_training=self.is_training, name='g_h4/batch_norm')

            net_h5 = UpSample(net_h4, size=[s2, s2], method=1, align_corners=False, name='g_h5/upsample2d')
            net_h5 = Conv2d(net_h5, 3, 3, gf_dim, 1, 1, name='g_h5/conv2d', padding='SAME')
            net_h5 = batch_normalization(net_h5, activation_fn=tf.nn.relu, is_training=self.is_training, name='g_h5/batch_norm')

            net_ho = UpSample(net_h5, size=[s, s], method=1, align_corners=False, name='g_ho/upsample2d')
            net_ho = Conv2d(net_ho, 3, 3, c_dim, 1, 1, name='g_ho/conv2d', padding='SAME', biased=True) ## biased = True

            self.outputs = tf.nn.tanh(net_ho)
            self.logits = net_ho

class Discriminator:
    def __init__(self, input_image, input_rnn, is_training, reuse):
        self.input_image = input_image
        self.input_rnn = input_rnn
        self.is_training = is_training
        self.reuse = reuse
        self.df_dim = 64
        self.t_dim = 128
        self.image_size = 64
        self._build_model()

    def _build_model(self):
        s = self.image_size
        s2, s4, s8, s16 = int(s/2), int(s/4), int(s/8), int(s/16)

        df_dim = self.df_dim
        t_dim = self.t_dim

        with tf.variable_scope("discriminator", reuse=self.reuse):
            net_h0 = Conv2d(self.input_image, 4, 4, df_dim, 2, 2, name='d_h0/conv2d', activation_fn=tf.nn.leaky_relu, padding='SAME', biased=True)

            net_h1 = Conv2d(net_h0, 4, 4, df_dim*2, 2, 2, name='d_h1/conv2d', padding='SAME')
            net_h1 = batch_normalization(net_h1, activation_fn=tf.nn.leaky_relu, is_training=self.is_training, name='d_h1/batchnorm')

            net_h2 = Conv2d(net_h1, 4, 4, df_dim*4, 2, 2, name='d_h2/conv2d', padding='SAME')
            net_h2 = batch_normalization(net_h2, activation_fn=tf.nn.leaky_relu, is_training=self.is_training, name='d_h2/batchnorm')

            net_h3 = Conv2d(net_h2, 4, 4, df_dim*8, 2, 2, name='d_h3/conv2d', padding='SAME')
            net_h3 = batch_normalization(net_h3, activation_fn=None, is_training=self.is_training, name='d_h3/batchnorm')

            net = Conv2d(net_h3, 1, 1, df_dim*2, 1, 1, name='d_h4_res/conv2d')
            net = batch_normalization(net, activation_fn=tf.nn.leaky_relu, is_training=self.is_training, name='d_h4_res/batchnorm')
            net = Conv2d(net, 3, 3, df_dim*2, 1, 1, name='d_h4_res/conv2d2', padding='SAME')
            net = batch_normalization(net, activation_fn=tf.nn.leaky_relu, is_training=self.is_training, name='d_h4_res/batchnorm2')
            net = Conv2d(net, 3, 3, df_dim*8, 1, 1, name='d_h4_res/conv2d3', padding='SAME')
            net = batch_normalization(net, activation_fn=None, is_training=self.is_training, name='d_h4_res/batchnorm3')

            net_h4 = add([net_h3, net], name='d_h4/add')
            net_h4_outputs = tf.nn.leaky_relu(net_h4)

            net_txt = fc(self.input_rnn, num_out=t_dim, activation_fn=tf.nn.leaky_relu, name='d_reduce_txt/dense')
            net_txt = tf.expand_dims(net_txt, axis=1, name='d_txt/expanddim1')
            net_txt = tf.expand_dims(net_txt, axis=1, name='d_txt/expanddim2')
            net_txt = tf.tile(net_txt, [1, 4, 4, 1], name='d_txt/tile')
            
            net_h4_concat = concat([net_h4_outputs, net_txt], axis=3, name='d_h3_concat')

            net_h4 = Conv2d(net_h4_concat, 1, 1, df_dim*8, 1, 1, name='d_h3/conv2d_2')
            net_h4 = batch_normalization(net_h4, activation_fn=tf.nn.leaky_relu, is_training=self.is_training, name='d_h3/batch_norm_2')

            net_ho = Conv2d(net_h4, s16, s16, 1, s16, s16, name='d_ho/conv2d', biased=True) # biased = True

            self.outputs = tf.nn.sigmoid(net_ho)
            self.logits = net_ho

class rnn_encoder:
    def __init__(self, input_seqs, is_training, reuse):
        self.input_seqs = input_seqs
        self.is_training = is_training
        self.reuse = reuse
        self.t_dim = 128  
        self.rnn_hidden_size = 128
        self.vocab_size = 8000
        self.word_embedding_size = 256
        self.keep_prob = 1.0
        self.batch_size = 64
        self._build_model()

    def _build_model(self):
        w_init = tf.random_normal_initializer(stddev=0.02)
        LSTMCell = tf.contrib.rnn.BasicLSTMCell

        with tf.variable_scope("rnnftxt", reuse=self.reuse):
            word_embed_matrix = tf.get_variable('rnn/wordembed', 
                shape=(self.vocab_size, self.word_embedding_size),
                initializer=tf.random_normal_initializer(stddev=0.02),
                dtype=tf.float32)
            embedded_word_ids = tf.nn.embedding_lookup(word_embed_matrix, self.input_seqs)

            # RNN encoder
            LSTMCell = tf.contrib.rnn.BasicLSTMCell(self.t_dim, reuse=self.reuse)
            initial_state = LSTMCell.zero_state(self.batch_size, dtype=tf.float32)
            
            rnn_net = tf.nn.dynamic_rnn(cell=LSTMCell,
                                    inputs=embedded_word_ids,
                                    initial_state=initial_state,
                                    dtype=np.float32,
                                    time_major=False,
                                    scope='rnn/dynamic')

            self.rnn_net = rnn_net
            self.outputs = rnn_net[0][:, -1, :]

class cnn_encoder:
    def __init__(self, inputs, is_training=True, reuse=False):
        self.inputs = inputs
        self.is_training = is_training
        self.reuse = reuse
        self.df_dim = 64
        self.t_dim = 128
        self._build_model()

    def _build_model(self):
        df_dim = self.df_dim

        with tf.variable_scope('cnnftxt', reuse=self.reuse):
            net_h0 = Conv2d(self.inputs, 4, 4, df_dim, 2, 2, name='cnnf/h0/conv2d', activation_fn=tf.nn.leaky_relu, padding='SAME', biased=True)
            net_h1 = Conv2d(net_h0, 4, 4, df_dim*2, 2, 2, name='cnnf/h1/conv2d', padding='SAME')
            net_h1 = batch_normalization(net_h1, activation_fn=tf.nn.leaky_relu, is_training=self.is_training, name='cnnf/h1/batch_norm')

            net_h2 = Conv2d(net_h1, 4, 4, df_dim*4, 2, 2, name='cnnf/h2/conv2d', padding='SAME')
            net_h2 = batch_normalization(net_h2, activation_fn=tf.nn.leaky_relu, is_training=self.is_training, name='cnnf/h2/batch_norm')

            net_h3 = Conv2d(net_h2, 4, 4, df_dim*8, 2, 2, name='cnnf/h3/conv2d', padding='SAME')
            net_h3 = batch_normalization(net_h3, activation_fn=tf.nn.leaky_relu, is_training=self.is_training, name='cnnf/h3/batch_norm')

            net_h4 = flatten(net_h3, name='cnnf/h4/flatten')
            net_h4 = fc(net_h4, num_out=self.t_dim, name='cnnf/h4/embed', biased=False)
        
        self.outputs = net_h4

In [3]:
import pandas as pd
import os
import scipy
from scipy.io import loadmat
import re
import string
import random
import time
import argparse

In [4]:
vocab = np.load(r'C:\Users\Stuti pandey\Documents\text-to-image dictionary\vocab.npy')
print('there are {} vocabularies in total'.format(len(vocab)))

there are 6375 vocabularies in total


In [5]:
word2Id_dict = dict(np.load(r"C:\Users\Stuti pandey\Documents\text-to-image dictionary\word2Id.npy"))
id2word_dict = dict(np.load(r"C:\Users\Stuti pandey\Documents\text-to-image dictionary\id2Word.npy"))

In [6]:
word2Id_dict

{'everyday': '5919',
 'kin': '4103',
 'door': '408',
 'travel': '4246',
 'u': '1181',
 'longi': '5679',
 'carri': '3556',
 'gas': '5094',
 'bookcas': '2028',
 'insd': '5412',
 'extrud': '3600',
 'smartphon': '893',
 'barrow': '5783',
 'dy': '3909',
 'forc': '689',
 'where': '2750',
 'cornet': '3545',
 'wilt': '2694',
 'yeklow': '4415',
 'heavi': '3290',
 'ocnic': '4335',
 'unsymmetr': '4136',
 'paperlik': '4659',
 'showcas': '3985',
 'submerg': '1877',
 'seclud': '6235',
 'perpendicular': '3915',
 'curvac': '4728',
 'globe': '2864',
 'sweater': '2009',
 'center': '2449',
 'feather': '2857',
 'fingernail': '4707',
 'affect': '6325',
 'doorway': '1115',
 'glossi': '2984',
 'trumpit': '3377',
 'alot': '3407',
 'outter': '4825',
 'greyish': '3558',
 'atch': '5913',
 'utensil': '2203',
 'strawberri': '5040',
 'peridecel': '6263',
 'pettel': '5265',
 'bedspread': '483',
 'wort': '5928',
 'snap': '5817',
 'ontop': '4266',
 'pompom': '3299',
 'difficulti': '5940',
 'nucleus': '5917',
 'unpeel'

In [7]:
train_images = np.load(r"C:\Users\Stuti pandey\Documents\text-to-image\train_images.npy", encoding='latin1')
train_captions = np.load(r"C:\Users\Stuti pandey\Documents\text-to-image\train_captions.npy", encoding='latin1')

In [8]:
len(train_images)

7370

In [9]:
len(train_captions)

7370

In [10]:
def IdList2sent(caption):
    sentence = []
    for ID in caption:
        if ID != word2Id_dict['<PAD>']:
            sentence.append(id2word_dict[ID])

    return sentence

print('----example of captions[0]--------')
for caption in train_captions[0]:
    print(IdList2sent(caption))

----example of captions[0]--------
['this', 'flower', 'has', 'petal', 'that', 'are', 'orang', 'with', 'brown', 'spot', 'and', 'orang', 'stamen']
['the', 'flower', 'has', 'yellow', 'petal', 'with', 'brown', 'stamen', 'and', 'green', 'pedicel']
['this', 'flower', 'is', 'orang', 'and', 'purpl', 'in', 'color', 'with', 'petal', 'that', 'are', 'spot']
['a', 'curl', 'of', 'yellow', 'petal', 'with', 'purpl', 'leopard', 'spot', 'curl', 'up', 'with', 'stamen', 'hang', 'below']
['this', 'flower', 'has', 'petal', 'that', 'are', 'orang', 'with', 'dark', 'spot']
['the', 'petal', 'of', 'the', 'flower', 'are', 'orang', 'in', 'color', 'with', 'brown', 'speckl', 'dot']
['this', 'flower', 'has', 'petal', 'that', 'are', 'tellow', 'and', 'has', 'black', 'spot']
['this', 'flower', 'has', 'long', 'orang', 'petal', 'with', 'dark', 'spot', 'lead', 'to', 'the', 'center']
['this', 'flower', 'has', 'orang', 'petal', 'with', 'dark', 'spot', 'and', 'fold', 'end', 'orient', 'away', 'from', 'a', 'group', 'of', 'long'

In [11]:
captions_list = []
for captions in train_captions:
    assert len(captions) >= 5
    captions_list.append(captions[:5])

In [12]:
train_captions = np.concatenate(captions_list, axis=0) 


In [13]:
n_captions_train = len(train_captions)
n_captions_per_image = 5
n_images_train = len(train_images)

In [14]:
print('Total captions: ', n_captions_train)
print('----example of captions[0] (modified)--------')
for caption in train_captions[:5]:
    print(IdList2sent(caption))

Total captions:  36850
----example of captions[0] (modified)--------
['this', 'flower', 'has', 'petal', 'that', 'are', 'orang', 'with', 'brown', 'spot', 'and', 'orang', 'stamen']
['the', 'flower', 'has', 'yellow', 'petal', 'with', 'brown', 'stamen', 'and', 'green', 'pedicel']
['this', 'flower', 'is', 'orang', 'and', 'purpl', 'in', 'color', 'with', 'petal', 'that', 'are', 'spot']
['a', 'curl', 'of', 'yellow', 'petal', 'with', 'purpl', 'leopard', 'spot', 'curl', 'up', 'with', 'stamen', 'hang', 'below']
['this', 'flower', 'has', 'petal', 'that', 'are', 'orang', 'with', 'dark', 'spot']


In [15]:
lr = 0.0002
lr_decay = 0.5      
decay_every = 100  
beta1 = 0.5

In [16]:
z_dim = 512         # Noise dimension
image_size = 64     # 64 x 64
c_dim = 3           # for rgb
batch_size = 64
ni = int(np.ceil(np.sqrt(batch_size)))

In [17]:
### Testing setting
sample_size = batch_size
sample_seed = np.random.normal(loc=0.0, scale=1.0, size=(sample_size, z_dim)).astype(np.float32)

In [18]:
sample_sentence = ["the flower shown has yellow anther red pistil and bright red petals."] * int(sample_size/ni) + \
                  ["this flower has petals that are yellow, white and purple and has dark lines"] * int(sample_size/ni) + \
                  ["the petals on this flower are white with a yellow center"] * int(sample_size/ni) + \
                  ["this flower has a lot of small round pink petals."] * int(sample_size/ni) + \
                  ["this flower is orange in color, and has petals that are ruffled and rounded."] * int(sample_size/ni) + \
                  ["the flower has yellow petals and the center of it is brown."] * int(sample_size/ni) + \
                  ["this flower has petals that are blue and white."] * int(sample_size/ni) +\
                  ["these white flowers have petals that start off white in color and end in a white towards the tips."] * int(sample_size/ni)

In [19]:
def sent2IdList(line, MAX_SEQ_LENGTH=20):
    MAX_SEQ_LIMIT = MAX_SEQ_LENGTH
    padding = 0
    prep_line = re.sub('[%s]' % re.escape(string.punctuation), ' ', line.rstrip())
    prep_line = prep_line.replace('-', ' ')
    prep_line = prep_line.replace('-', ' ')
    prep_line = prep_line.replace('  ', ' ')
    prep_line = prep_line.replace('.', '')
    tokens = prep_line.split(' ')
    tokens = [
        tokens[i] for i in range(len(tokens))
        if tokens[i] != ' ' and tokens[i] != ''
    ]
    l = len(tokens)
    padding = MAX_SEQ_LIMIT - l
    for i in range(padding):
        tokens.append('<PAD>')
    
    line = [
        word2Id_dict[tokens[k]]
        if tokens[k] in word2Id_dict else word2Id_dict['<RARE>']
        for k in range(len(tokens))
    ]

    return line

In [20]:
for i, sent in enumerate(sample_sentence):
    sample_sentence[i] = sent2IdList(sent)

In [21]:
print(sample_sentence[0])


['2435', '2428', '2505', '2431', '2437', '2465', '2446', '2457', '2429', '2455', '2446', '6374', '6372', '6372', '6372', '6372', '6372', '6372', '6372', '6372']


In [22]:
def save(saver, sess, logdir, step):
    model_name = 'model.ckpt'
    checkpoint_path = os.path.join(logdir, model_name)
    
    if not os.path.exists(logdir):
        os.makedirs(logdir)
    saver.save(sess, checkpoint_path, global_step=step)
    print('The checkpoint has been created.')


In [23]:
def load(saver, sess, ckpt_path):
    saver.restore(sess, ckpt_path)
    print("Restored model parameters from {}".format(ckpt_path))

In [24]:
#train
t_real_image = tf.placeholder('float32',[batch_size,image_size,image_size,3],name='real_image')
t_wrong_image = tf.placeholder('float32',[batch_size,image_size,image_size,3],name='wrong_image')
t_real_caption = tf.placeholder(dtype= tf.int64 ,shape=[batch_size,None],name='real_caption_input')
t_wrong_caption = tf.placeholder(dtype=tf.int64,shape=[batch_size,None],name='wrong_caption_input')
t_z = tf.placeholder(tf.float32,[batch_size , z_dim],name='z_noise')

In [25]:
# Training Phase - CNN - RNN mapping
net_cnn = cnn_encoder(t_real_image,is_training=True, reuse=False)
x = net_cnn.outputs
net_rnn = rnn_encoder(t_real_caption,is_training=True, reuse=False)
v= net_rnn.outputs
x_wrong =cnn_encoder(t_wrong_image,is_training=True, reuse=True).outputs
v_wrong = rnn_encoder(t_wrong_caption,is_training=True, reuse=True).outputs


In [26]:
def cosine_similarity(v1, v2):
    cost = tf.reduce_sum(tf.multiply(v1, v2), 1) / (tf.sqrt(tf.reduce_sum(tf.multiply(v1, v1), 1)) * tf.sqrt(tf.reduce_sum(tf.multiply(v2, v2), 1)))
    return cost

In [27]:
alpha =0.2
rnn_loss = tf.reduce_mean(tf.maximum(0.,alpha - cosine_similarity(x,v) + cosine_similarity(x,v_wrong)))+ tf.reduce_mean(tf.maximum(0.,alpha - cosine_similarity(x,v) + cosine_similarity(x_wrong,v)))

In [28]:
# Training Phase - GAN


In [29]:
net_rnn = rnn_encoder(t_real_caption,is_training=False, reuse=True)
net_fake_image = Generator(t_z,net_rnn.outputs,is_training=True, reuse=False)

net_disc_fake = Discriminator(net_fake_image.outputs,net_rnn.outputs,is_training=True, reuse=False)
disc_fake_logits = net_disc_fake.logits

net_disc_real = Discriminator(t_real_image ,net_rnn.outputs,is_training=True, reuse=True)
disc_real_logits = net_disc_real.logits

net_disc_mismatch = Discriminator(t_real_image ,rnn_encoder(t_wrong_caption, is_training=False, reuse=True).outputs,
                                is_training=True, reuse=True)
disc_mismatch_logits = net_disc_mismatch.logits


In [30]:
d_loss1 = tf.reduce_mean(tf.nn.sigmoid_cross_entropy_with_logits(logits=disc_real_logits,     labels=tf.ones_like(disc_real_logits),      name='d1'))
d_loss2 = tf.reduce_mean(tf.nn.sigmoid_cross_entropy_with_logits(logits=disc_mismatch_logits, labels=tf.zeros_like(disc_mismatch_logits), name='d2'))
d_loss3 = tf.reduce_mean(tf.nn.sigmoid_cross_entropy_with_logits(logits=disc_fake_logits,     labels=tf.zeros_like(disc_fake_logits),     name='d3'))
d_loss = d_loss1 + (d_loss2 + d_loss3) * 0.5

g_loss = tf.reduce_mean(tf.nn.sigmoid_cross_entropy_with_logits(logits=disc_fake_logits, labels=tf.ones_like(disc_fake_logits), name='g'))


In [31]:
#Testing Phase
        

In [32]:
net_g = Generator(t_z, rnn_encoder(t_real_caption, is_training=False, reuse=True).outputs,
                    is_training=False, reuse=True)

rnn_vars = [var for var in tf.trainable_variables() if 'rnn' in var.name]
g_vars = [var for var in tf.trainable_variables() if 'generator' in var.name]
d_vars = [var for var in tf.trainable_variables() if 'discrim' in var.name]
cnn_vars = [var for var in tf.trainable_variables() if 'cnn' in var.name]

update_ops_D = [var for var in tf.get_collection(tf.GraphKeys.UPDATE_OPS) if 'discrim' in var.name]
update_ops_G = [var for var in tf.get_collection(tf.GraphKeys.UPDATE_OPS) if 'generator' in var.name]
update_ops_CNN = [var for var in tf.get_collection(tf.GraphKeys.UPDATE_OPS) if 'cnn' in var.name]

print('----------Update_ops_D--------')
for var in update_ops_D:
        print(var.name)
print('----------Update_ops_G--------')
for var in update_ops_G:
        print(var.name)
print('----------Update_ops_CNN--------')
for var in update_ops_CNN:
        print(var.name)


----------Update_ops_D--------
discriminator/d_h1/batchnorm/AssignMovingAvg
discriminator/d_h1/batchnorm/AssignMovingAvg_1
discriminator/d_h2/batchnorm/AssignMovingAvg
discriminator/d_h2/batchnorm/AssignMovingAvg_1
discriminator/d_h3/batchnorm/AssignMovingAvg
discriminator/d_h3/batchnorm/AssignMovingAvg_1
discriminator/d_h4_res/batchnorm/AssignMovingAvg
discriminator/d_h4_res/batchnorm/AssignMovingAvg_1
discriminator/d_h4_res/batchnorm2/AssignMovingAvg
discriminator/d_h4_res/batchnorm2/AssignMovingAvg_1
discriminator/d_h4_res/batchnorm3/AssignMovingAvg
discriminator/d_h4_res/batchnorm3/AssignMovingAvg_1
discriminator/d_h3/batch_norm_2/AssignMovingAvg
discriminator/d_h3/batch_norm_2/AssignMovingAvg_1
discriminator_1/d_h1/batchnorm/AssignMovingAvg
discriminator_1/d_h1/batchnorm/AssignMovingAvg_1
discriminator_1/d_h2/batchnorm/AssignMovingAvg
discriminator_1/d_h2/batchnorm/AssignMovingAvg_1
discriminator_1/d_h3/batchnorm/AssignMovingAvg
discriminator_1/d_h3/batchnorm/AssignMovingAvg_1
dis

In [33]:
checkpoint_dir = './checkpoint'


In [34]:
with tf.variable_scope('learning_rate'):
        lr_v = tf.Variable(lr, trainable=False)

with tf.control_dependencies(update_ops_D):
        d_optim = tf.train.AdamOptimizer(lr_v, beta1=beta1).minimize(d_loss, var_list=d_vars)

with tf.control_dependencies(update_ops_G):
    g_optim = tf.train.AdamOptimizer(lr_v, beta1=beta1).minimize(g_loss, var_list=g_vars)

with tf.control_dependencies(update_ops_CNN):
        grads, _ = tf.clip_by_global_norm(tf.gradients(rnn_loss, rnn_vars + cnn_vars), 10)
        optimizer = tf.train.AdamOptimizer(lr_v, beta1=beta1)
        rnn_optim = optimizer.apply_gradients(zip(grads, rnn_vars + cnn_vars))

sess = tf.Session(config=tf.ConfigProto(allow_soft_placement=True))
init = tf.global_variables_initializer()
sess.run(init)

saver = tf.train.Saver(var_list=tf.global_variables(), max_to_keep=5)

ckpt = tf.train.get_checkpoint_state(checkpoint_dir)
if ckpt and ckpt.model_checkpoint_path:
    loader = tf.train.Saver(var_list=tf.global_variables())
    load_step = int(os.path.basename(ckpt.model_checkpoint_path).split('-')[1])
    load(loader, sess, ckpt.model_checkpoint_path)
else:
    print('no checkpoints find.')



no checkpoints find.


In [35]:
import threading
import scipy.ndimage as ndi
from skimage import transform
from skimage import exposure
import skimage

In [36]:
def apply_transform(x, transform_matrix, channel_index=2, fill_mode='nearest', cval=0., order=1):
    x = np.rollaxis(x, channel_index, 0)
    final_affine_matrix = transform_matrix[:2, :2]
    final_offset = transform_matrix[:2, 2]
    channel_images = [ndi.interpolation.affine_transform(x_channel, final_affine_matrix,
                      final_offset, order=order, mode=fill_mode, cval=cval) for x_channel in x]
    x = np.stack(channel_images, axis=0)
    x = np.rollaxis(x, 0, channel_index+1)
    return x

def transform_matrix_offset_center(matrix, x, y):
    o_x = float(x) / 2 + 0.5
    o_y = float(y) / 2 + 0.5
    offset_matrix = np.array([[1, 0, o_x], [0, 1, o_y], [0, 0, 1]])
    reset_matrix = np.array([[1, 0, -o_x], [0, 1, -o_y], [0, 0, 1]])
    transform_matrix = np.dot(np.dot(offset_matrix, matrix), reset_matrix)
    return transform_matrix

def get_random_int(min=0, max=10, number=5):
    """Return a list of random integer by the given range and quantity.
    Examples
    ---------
    >>> r = get_random_int(min=0, max=10, number=5)
    ... [10, 2, 3, 3, 7]
    """
    return [random.randint(min,max) for p in range(0,number)]

def threading_data(data=None, fn=None, **kwargs):
    def apply_fn(results, i, data, kwargs):
        results[i] = fn(data, **kwargs)

    ## start multi-threaded reading.
    results = [None] * len(data) ## preallocate result list
    threads = []
    for i in range(len(data)):
        t = threading.Thread(
                        name='threading_and_return',
                        target=apply_fn,
                        args=(results, i, data[i], kwargs)
                        )
        t.start()
        threads.append(t)

    for t in threads:
        t.join()

    return np.asarray(results)

def flip_axis(x, axis, is_random=False):
    if is_random:
        factor = np.random.uniform(-1, 1)
        if factor > 0:
            x = np.asarray(x).swapaxes(axis, 0)
            x = x[::-1, ...]
            x = x.swapaxes(0, axis)
            return x
        else:
            return x
    else:
        x = np.asarray(x).swapaxes(axis, 0)
        x = x[::-1, ...]
        x = x.swapaxes(0, axis)
        return x
    
def imresize(x, size=[100, 100], interp='bilinear', mode=None):
    if x.shape[-1] == 1:
        # greyscale
        x = scipy.misc.imresize(x[:,:,0], size, interp=interp, mode=mode)
        return x[:, :, np.newaxis]
    elif x.shape[-1] == 3:
        # rgb, bgr ..
        return scipy.misc.imresize(x, size, interp=interp, mode=mode)
    else:
        raise Exception("Unsupported channel %d" % x.shape[-1])

def rotation(x, rg=20, is_random=False, row_index=0, col_index=1, channel_index=2,
                    fill_mode='nearest', cval=0.):
    if is_random:
        theta = np.pi / 180 * np.random.uniform(-rg, rg)
    else:
        theta = np.pi /180 * rg
    rotation_matrix = np.array([[np.cos(theta), -np.sin(theta), 0],
                                [np.sin(theta), np.cos(theta), 0],
                                [0, 0, 1]])

    h, w = x.shape[row_index], x.shape[col_index]
    transform_matrix = transform_matrix_offset_center(rotation_matrix, h, w)
    x = apply_transform(x, transform_matrix, channel_index, fill_mode, cval)
    return x

def crop(x, wrg, hrg, is_random=False, row_index=0, col_index=1, channel_index=2):
    h, w = x.shape[row_index], x.shape[col_index]
    assert (h > hrg) and (w > wrg), "The size of cropping should smaller than the original image"
    if is_random:
        h_offset = int(np.random.uniform(0, h-hrg) -1)
        w_offset = int(np.random.uniform(0, w-wrg) -1)
        return x[h_offset: hrg+h_offset ,w_offset: wrg+w_offset]
    else:   # central crop
        h_offset = int(np.floor((h - hrg)/2.))
        w_offset = int(np.floor((w - wrg)/2.))
        h_end = h_offset + hrg
        w_end = w_offset + wrg
        return x[h_offset: h_end, w_offset: w_end]        
        

def prepro_img(x, mode=None):
    # rescale [0, 255] --> (-1, 1), random flip, crop, rotate

    if mode=='train':
        x = flip_axis(x, axis=1, is_random=True)
        x = rotation(x, rg=16, is_random=True, fill_mode='nearest')
        x = imresize(x, size=[64+15, 64+15], interp='bilinear', mode=None)
        x = crop(x, wrg=64, hrg=64, is_random=True)
        x = x / (255. / 2.)
        x = x - 1.
        # x = x * 0.9999

    return x

In [37]:
## Save images
def merge(images, size):
    h, w = images.shape[1], images.shape[2]
    img = np.zeros((h * size[0], w * size[1], 3))
    for idx, image in enumerate(images):
        i = idx % size[1]
        j = idx // size[1]
        img[j*h:j*h+h, i*w:i*w+w, :] = image
    return img

def imsave(images, size, path):
    return scipy.misc.imsave(path, merge(images, size))

def save_images(images, size, image_path):
    return imsave(images, size, image_path)

In [38]:
n_epoch = 600
n_batch_epoch = int(n_images_train / batch_size)
for epoch in range(n_epoch):
    start_time = time.time()

    if epoch !=0 and (epoch % decay_every == 0):
            new_lr_decay = lr_decay ** (epoch // decay_every)
            sess.run(tf.assign(lr_v, lr * new_lr_decay))
            log = " ** new learning rate: %f" % (lr * new_lr_decay)
            print(log)
            
    elif epoch == 0:
            log = " ** init lr: %f  decay_every_epoch: %d, lr_decay: %f" % (lr, decay_every, lr_decay)
            print(log)

    for step in range(n_batch_epoch):
        step_time = time.time()

        ## get matched text & image
        idexs = get_random_int(min=0, max=n_captions_train-1, number=batch_size)
        b_real_caption = train_captions[idexs]
        b_real_images = train_images[np.floor(np.asarray(idexs).astype('float')/n_captions_per_image).astype('int')]

        """ check for loading right images
        save_images(b_real_images, [ni, ni], 'train_samples/train_00.png')
        for caption in b_real_caption[:8]:
        print(IdList2sent(caption))
        exit()
        """

        ## get wrong caption & wrong image
        idexs = get_random_int(min=0, max=n_captions_train-1, number=batch_size)
        b_wrong_caption = train_captions[idexs]
        idexs2 = get_random_int(min=0, max=n_images_train-1, number=batch_size)
        b_wrong_images = train_images[idexs2]

        ## get noise
        b_z = np.random.normal(loc=0.0, scale=1.0, size=(batch_size, z_dim)).astype(np.float32)

        b_real_images = threading_data(b_real_images, prepro_img, mode='train')   # [0, 255] --> [-1, 1] + augmentation
        b_wrong_images = threading_data(b_wrong_images, prepro_img, mode='train')

        ## update RNN
        if epoch < 80:
            errRNN, _ = sess.run([rnn_loss, rnn_optim], feed_dict={
                                                t_real_image : b_real_images,
                                                t_wrong_image : b_wrong_images,
                                                t_real_caption : b_real_caption,
                                                t_wrong_caption : b_wrong_caption})
        else:
            errRNN = 0

        ## updates D
        errD, _ = sess.run([d_loss, d_optim], feed_dict={
                            t_real_image : b_real_images,
                            t_wrong_caption : b_wrong_caption,
                            t_real_caption : b_real_caption,
                            t_z : b_z})
        ## updates G
        errG, _ = sess.run([g_loss, g_optim], feed_dict={
                            t_real_caption : b_real_caption,
                            t_z : b_z})

        print("Epoch: [%2d/%2d] [%4d/%4d] time: %4.4fs, d_loss: %.8f, g_loss: %.8f, rnn_loss: %.8f" \
                        % (epoch, n_epoch, step, n_batch_epoch, time.time() - step_time, errD, errG, errRNN))
        
        if (epoch + 1) % 1 == 0:
            print(" ** Epoch %d took %fs" % (epoch, time.time()-start_time))
            img_gen, rnn_out = sess.run([net_g.outputs, net_rnn.outputs], feed_dict={
                                        t_real_caption : sample_sentence,
                                        t_z : sample_seed})

            save_images(img_gen, [ni, ni],r"C:\Users\Stuti pandey\Documents\train_samples\train_{:02d}.png".format(epoch))

        if (epoch != 0) and (epoch % 10) == 0:
            save(saver, sess, checkpoint_dir, epoch)
            print("[*] Save checkpoints SUCCESS!")

#testData = os.path.join('dataset', 'testData.pkl')

 ** init lr: 0.000200  decay_every_epoch: 100, lr_decay: 0.500000
Epoch: [ 0/600] [   0/ 115] time: 18.3452s, d_loss: 2.71513557, g_loss: 0.05987190, rnn_loss: 0.39814478
 ** Epoch 0 took 18.347862s
Epoch: [ 0/600] [   1/ 115] time: 0.7520s, d_loss: 7.58284616, g_loss: 0.98363864, rnn_loss: 0.41578957
 ** Epoch 0 took 19.467037s
Epoch: [ 0/600] [   2/ 115] time: 0.7689s, d_loss: 3.43822098, g_loss: 5.90367985, rnn_loss: 0.36642528
 ** Epoch 0 took 20.413499s
Epoch: [ 0/600] [   3/ 115] time: 0.7793s, d_loss: 3.13539481, g_loss: 3.94523931, rnn_loss: 0.43461281
 ** Epoch 0 took 21.376362s
Epoch: [ 0/600] [   4/ 115] time: 0.7700s, d_loss: 2.42501211, g_loss: 4.19036770, rnn_loss: 0.39950821
 ** Epoch 0 took 22.316883s
Epoch: [ 0/600] [   5/ 115] time: 0.7590s, d_loss: 1.76547170, g_loss: 7.29295969, rnn_loss: 0.37671489
 ** Epoch 0 took 23.251359s
Epoch: [ 0/600] [   6/ 115] time: 0.7779s, d_loss: 2.24530554, g_loss: 8.58616924, rnn_loss: 0.36278740
 ** Epoch 0 took 24.201831s
Epoch: [ 

Epoch: [ 0/600] [  62/ 115] time: 0.7641s, d_loss: 1.41542685, g_loss: 2.52398872, rnn_loss: 0.25682741
 ** Epoch 0 took 81.715497s
Epoch: [ 0/600] [  63/ 115] time: 0.7551s, d_loss: 1.24338830, g_loss: 3.65780592, rnn_loss: 0.25648847
 ** Epoch 0 took 82.697972s
Epoch: [ 0/600] [  64/ 115] time: 0.7590s, d_loss: 1.20103765, g_loss: 2.72703576, rnn_loss: 0.20288433
 ** Epoch 0 took 83.682357s
Epoch: [ 0/600] [  65/ 115] time: 0.7705s, d_loss: 1.23242605, g_loss: 3.01540041, rnn_loss: 0.26951608
 ** Epoch 0 took 84.667296s
Epoch: [ 0/600] [  66/ 115] time: 0.8807s, d_loss: 1.22731256, g_loss: 3.14055920, rnn_loss: 0.27703735
 ** Epoch 0 took 85.755400s
Epoch: [ 0/600] [  67/ 115] time: 0.7739s, d_loss: 1.45392585, g_loss: 1.58053541, rnn_loss: 0.33409590
 ** Epoch 0 took 86.751675s
Epoch: [ 0/600] [  68/ 115] time: 0.7490s, d_loss: 1.50471663, g_loss: 4.39738178, rnn_loss: 0.21008699
 ** Epoch 0 took 87.856745s
Epoch: [ 0/600] [  69/ 115] time: 0.8904s, d_loss: 1.48695707, g_loss: 2.504

Epoch: [ 1/600] [   9/ 115] time: 0.8358s, d_loss: 1.62716913, g_loss: 1.35084224, rnn_loss: 0.19786574
 ** Epoch 1 took 11.181555s
Epoch: [ 1/600] [  10/ 115] time: 0.9604s, d_loss: 1.20103455, g_loss: 3.57691956, rnn_loss: 0.24869949
 ** Epoch 1 took 12.406279s
Epoch: [ 1/600] [  11/ 115] time: 0.8668s, d_loss: 1.03535628, g_loss: 3.23055863, rnn_loss: 0.23240247
 ** Epoch 1 took 13.538391s
Epoch: [ 1/600] [  12/ 115] time: 0.7763s, d_loss: 1.06627107, g_loss: 1.42587042, rnn_loss: 0.23933360
 ** Epoch 1 took 14.589553s
Epoch: [ 1/600] [  13/ 115] time: 0.7694s, d_loss: 1.11741912, g_loss: 2.86746740, rnn_loss: 0.15651591
 ** Epoch 1 took 15.680100s
Epoch: [ 1/600] [  14/ 115] time: 0.7510s, d_loss: 0.83703452, g_loss: 3.23740172, rnn_loss: 0.17742155
 ** Epoch 1 took 16.705409s
Epoch: [ 1/600] [  15/ 115] time: 0.7697s, d_loss: 0.88866317, g_loss: 2.48376846, rnn_loss: 0.17257677
 ** Epoch 1 took 17.753284s
Epoch: [ 1/600] [  16/ 115] time: 0.8657s, d_loss: 0.88156813, g_loss: 2.645

Epoch: [ 1/600] [  72/ 115] time: 0.7440s, d_loss: 0.70701092, g_loss: 1.93126297, rnn_loss: 0.14953855
 ** Epoch 1 took 79.957589s
Epoch: [ 1/600] [  73/ 115] time: 0.7520s, d_loss: 0.52025330, g_loss: 1.98379588, rnn_loss: 0.15511915
 ** Epoch 1 took 80.975867s
Epoch: [ 1/600] [  74/ 115] time: 0.7490s, d_loss: 0.76648659, g_loss: 4.27851582, rnn_loss: 0.17766879
 ** Epoch 1 took 81.991182s
Epoch: [ 1/600] [  75/ 115] time: 0.7516s, d_loss: 1.04177272, g_loss: 0.51787084, rnn_loss: 0.12881443
 ** Epoch 1 took 83.010122s
Epoch: [ 1/600] [  76/ 115] time: 0.9505s, d_loss: 1.27486384, g_loss: 3.87774277, rnn_loss: 0.23537983
 ** Epoch 1 took 84.223877s
Epoch: [ 1/600] [  77/ 115] time: 0.9126s, d_loss: 0.91884494, g_loss: 1.17008758, rnn_loss: 0.17300768
 ** Epoch 1 took 85.398736s
Epoch: [ 1/600] [  78/ 115] time: 0.8630s, d_loss: 0.87433648, g_loss: 3.35111809, rnn_loss: 0.18560594
 ** Epoch 1 took 86.526012s
Epoch: [ 1/600] [  79/ 115] time: 0.7580s, d_loss: 0.78177893, g_loss: 1.415

Epoch: [ 2/600] [  19/ 115] time: 0.7600s, d_loss: 0.93414414, g_loss: 1.34330010, rnn_loss: 0.20266894
 ** Epoch 2 took 21.090715s
Epoch: [ 2/600] [  20/ 115] time: 0.7690s, d_loss: 1.05978394, g_loss: 2.35475302, rnn_loss: 0.14994285
 ** Epoch 2 took 22.201790s
Epoch: [ 2/600] [  21/ 115] time: 0.8926s, d_loss: 0.84585643, g_loss: 2.17989182, rnn_loss: 0.21554765
 ** Epoch 2 took 23.335758s
Epoch: [ 2/600] [  22/ 115] time: 0.8864s, d_loss: 0.84610379, g_loss: 1.47643125, rnn_loss: 0.18169367
 ** Epoch 2 took 24.465503s
Epoch: [ 2/600] [  23/ 115] time: 0.8557s, d_loss: 0.92248476, g_loss: 3.08389258, rnn_loss: 0.15699296
 ** Epoch 2 took 25.558579s
Epoch: [ 2/600] [  24/ 115] time: 0.7622s, d_loss: 1.48096943, g_loss: 0.66242599, rnn_loss: 0.16428682
 ** Epoch 2 took 26.584152s
Epoch: [ 2/600] [  25/ 115] time: 0.7722s, d_loss: 1.35832918, g_loss: 3.23369145, rnn_loss: 0.20482507
 ** Epoch 2 took 27.689437s
Epoch: [ 2/600] [  26/ 115] time: 0.9256s, d_loss: 0.78214991, g_loss: 2.583

...

Epoch: [348/600] [  65/ 115] time: 0.8466s, d_loss: 0.11261317, g_loss: 3.09389067, rnn_loss: 0.00000000
 ** Epoch 348 took 62.600850s
Epoch: [348/600] [  66/ 115] time: 0.7071s, d_loss: 0.07003798, g_loss: 3.99394798, rnn_loss: 0.00000000
 ** Epoch 348 took 63.525379s
Epoch: [348/600] [  67/ 115] time: 0.6852s, d_loss: 0.06417888, g_loss: 3.29476094, rnn_loss: 0.00000000
 ** Epoch 348 took 64.492792s
Epoch: [348/600] [  68/ 115] time: 0.8976s, d_loss: 0.10464039, g_loss: 3.25113964, rnn_loss: 0.00000000
 ** Epoch 348 took 65.608835s
Epoch: [348/600] [  69/ 115] time: 0.8398s, d_loss: 0.07005936, g_loss: 3.96765995, rnn_loss: 0.00000000
 ** Epoch 348 took 66.687922s
Epoch: [348/600] [  70/ 115] time: 0.7224s, d_loss: 0.00887819, g_loss: 5.89904737, rnn_loss: 0.00000000
 ** Epoch 348 took 67.631987s
Epoch: [348/600] [  71/ 115] time: 0.7370s, d_loss: 0.03378543, g_loss: 5.55196619, rnn_loss: 0.00000000
 ** Epoch 348 took 68.688725s
Epoch: [348/600] [  72/ 115] time: 0.8458s, d_loss: 0.1

Epoch: [349/600] [  11/ 115] time: 0.6981s, d_loss: 0.01668322, g_loss: 4.48286676, rnn_loss: 0.00000000
 ** Epoch 349 took 11.049273s
Epoch: [349/600] [  12/ 115] time: 0.6961s, d_loss: 0.02949658, g_loss: 3.50016594, rnn_loss: 0.00000000
 ** Epoch 349 took 11.946873s
Epoch: [349/600] [  13/ 115] time: 0.6981s, d_loss: 0.29016489, g_loss: 2.59460354, rnn_loss: 0.00000000
 ** Epoch 349 took 12.846469s
Epoch: [349/600] [  14/ 115] time: 0.7430s, d_loss: 0.06727310, g_loss: 3.09546304, rnn_loss: 0.00000000
 ** Epoch 349 took 13.839812s
Epoch: [349/600] [  15/ 115] time: 0.6961s, d_loss: 0.39562434, g_loss: 4.36929131, rnn_loss: 0.00000000
 ** Epoch 349 took 14.737424s
Epoch: [349/600] [  16/ 115] time: 0.7043s, d_loss: 0.57705665, g_loss: 3.17390299, rnn_loss: 0.00000000
 ** Epoch 349 took 15.641180s
Epoch: [349/600] [  17/ 115] time: 0.6968s, d_loss: 0.03504530, g_loss: 3.01328802, rnn_loss: 0.00000000
 ** Epoch 349 took 16.541450s
Epoch: [349/600] [  18/ 115] time: 0.8218s, d_loss: 0.0

Epoch: [349/600] [  72/ 115] time: 0.7300s, d_loss: 0.14176789, g_loss: 2.85799599, rnn_loss: 0.00000000
 ** Epoch 349 took 69.261571s
Epoch: [349/600] [  73/ 115] time: 0.6991s, d_loss: 0.03510063, g_loss: 3.84662628, rnn_loss: 0.00000000
 ** Epoch 349 took 70.232878s
Epoch: [349/600] [  74/ 115] time: 0.9455s, d_loss: 0.06048311, g_loss: 4.21911001, rnn_loss: 0.00000000
 ** Epoch 349 took 71.380852s
Epoch: [349/600] [  75/ 115] time: 0.8261s, d_loss: 0.09371157, g_loss: 3.24996853, rnn_loss: 0.00000000
 ** Epoch 349 took 72.404345s
Epoch: [349/600] [  76/ 115] time: 0.7175s, d_loss: 0.01468209, g_loss: 4.83952188, rnn_loss: 0.00000000
 ** Epoch 349 took 73.321652s
Epoch: [349/600] [  77/ 115] time: 0.6961s, d_loss: 0.10480310, g_loss: 4.15646029, rnn_loss: 0.00000000
 ** Epoch 349 took 74.323756s
Epoch: [349/600] [  78/ 115] time: 0.9395s, d_loss: 0.08202443, g_loss: 3.20013475, rnn_loss: 0.00000000
 ** Epoch 349 took 75.461714s
Epoch: [349/600] [  79/ 115] time: 0.7969s, d_loss: 0.3

The checkpoint has been created.
[*] Save checkpoints SUCCESS!
Epoch: [350/600] [  13/ 115] time: 0.7001s, d_loss: 0.04725278, g_loss: 2.91836858, rnn_loss: 0.00000000
 ** Epoch 350 took 71.932358s
The checkpoint has been created.
[*] Save checkpoints SUCCESS!
Epoch: [350/600] [  14/ 115] time: 0.7081s, d_loss: 0.34836024, g_loss: 3.14658070, rnn_loss: 0.00000000
 ** Epoch 350 took 77.862068s
The checkpoint has been created.
[*] Save checkpoints SUCCESS!
Epoch: [350/600] [  15/ 115] time: 0.7121s, d_loss: 0.05192453, g_loss: 4.15278912, rnn_loss: 0.00000000
 ** Epoch 350 took 83.147054s
The checkpoint has been created.
[*] Save checkpoints SUCCESS!
Epoch: [350/600] [  16/ 115] time: 0.7111s, d_loss: 0.07579209, g_loss: 3.64978933, rnn_loss: 0.00000000
 ** Epoch 350 took 88.476386s
The checkpoint has been created.
[*] Save checkpoints SUCCESS!
Epoch: [350/600] [  17/ 115] time: 0.7002s, d_loss: 0.03764914, g_loss: 5.33555508, rnn_loss: 0.00000000
 ** Epoch 350 took 94.029971s
The checkp

KeyboardInterrupt: 